In [1]:
import re
import csv
import sqlite3
import pandas as pd
from pathlib import Path

In [3]:
# Load the CSV file
csv_file = 'covid_submissions_all_info.csv'
data = pd.read_csv(csv_file, low_memory=False)

In [9]:
# Define a function to count the number of 'rule of five' violations
def rule_of_five_violations(row):
    violations = sum([
        row['HBD'] > 5,
        row['HBA'] > 10,
        row['MW'] >= 500,
        row['cLogP'] >= 5
    ])
    return violations

# Apply the function to the data
data['rule_of_five_violations'] = data.apply(rule_of_five_violations, axis=1)

# Filter out compounds that violate more than one rule
rule_of_five_data = data[data['rule_of_five_violations'] <= 1]

# Extract data for the 'compounds' and 'rule_of_five_compliant_compounds' tables
smiles_data = data[['CID', 'SMILES', 'HBD', 'HBA', 'MW', 'cLogP']].drop_duplicates()

# Select relevant columns for 'assays'
columns_of_interest = ['CID', 'f_avg_IC50', 'r_avg_IC50']
assay_data = data[columns_of_interest]

# Create a new SQLite database
database_file = 'assays_database.db'
conn = sqlite3.connect(database_file)
cursor = conn.cursor()

# Create the 'compounds' table 
cursor.execute('''
    CREATE TABLE IF NOT EXISTS compounds (
        CID TEXT PRIMARY KEY,
        SMILES TEXT,
        HBD INTEGER,
        HBA INTEGER,
        MW REAL,
        cLogP REAL
    );           
''')

# Create the 'rule_of_five_compliant_compounds' table
cursor.execute('''
    CREATE TABLE IF NOT EXISTS rule_of_five_compliant_compounds (
        CID TEXT PRIMARY KEY,
        SMILES TEXT,
        HBD INTEGER,
        HBA INTEGER,
        MW REAL,
        cLogP REAL
    );
''')

# Populate the 'compounds' table
for _, row in smiles_data.iterrows():
    cursor.execute('''
        INSERT OR IGNORE INTO compounds (CID, SMILES, HBD, HBA, MW, cLogP) 
        VALUES (?, ?, ?, ?, ?, ?)
    ''', (row['CID'], row['SMILES'], row['HBD'], row['HBA'], row['MW'], row['cLogP']))

# Populate the 'rule_of_five_compliant_compounds' table
for _, row in rule_of_five_data.iterrows():
    cursor.execute('''
        INSERT OR IGNORE INTO rule_of_five_compliant_compounds (CID, SMILES, HBD, HBA, MW, cLogP) 
        VALUES (?, ?, ?, ?, ?, ?)
    ''', (row['CID'], row['SMILES'], row['HBD'], row['HBA'], row['MW'], row['cLogP']))

# Create the 'assays' table with a foreign key
cursor.execute('''
    CREATE TABLE IF NOT EXISTS assays (
        CID TEXT,
        f_avg_IC50 REAL,
        r_avg_IC50 REAL,
        FOREIGN KEY (CID) REFERENCES compounds(CID)
    );
''')

# Populate the 'assays' data into the table
for _, row in assay_data.iterrows():
    cursor.execute('''
        INSERT INTO assays (CID, f_avg_IC50, r_avg_IC50) 
        VALUES (?, ?, ?)
    ''', (row['CID'], row['f_avg_IC50'], row['r_avg_IC50']))

# Commit changes and close the connection
conn.commit()

# Demonstrate an SQL query for joining the two tables
cursor.execute('''
    SELECT c.CID, c.SMILES, a.f_avg_IC50, a.r_avg_IC50
    FROM compounds c
    JOIN assays a ON c.CID = a.CID
''')

# Fetch and print the result of the query
joined_data = cursor.fetchall()
for row in joined_data:
    print(row)

conn.close()
print("Database and tables created successfully with the data.")

('ANT-DIA-3c79be55-1', 'N#Cc1ccccc1NC(=O)Cc1c[nH]c2ncccc12', None, None)
('ANT-DIA-3c79be55-2', 'N#Cc1ccccc1NC(=O)Cc1cccnc1', None, None)
('ANT-DIA-3c79be55-3', 'CCNc1ccc(C#N)c(NC(=O)Cc2c[nH]c3ncccc23)c1', None, None)
('ANT-DIA-3c79be55-4', 'CS(=O)(=O)Cc1ccc(C(=O)Nc2cccnc2)o1', None, None)
('ANT-DIA-3c79be55-5', 'O=C(Nc1cccnc1)c1ccc(N2CCC(O)CC2)o1', None, None)
('ROB-UNI-b2e39629-1', 'CCNc1ccc(C#N)cc1CCNS(C)(=O)=O', None, None)
('ROB-UNI-b2e39629-2', 'CS(=O)(=O)NCCc1c[nH]c2c(CCNS(C)(=O)=O)cc(Cl)cc12', None, None)
('ROB-UNI-b2e39629-3', 'CCn1cc(CCNS(C)(=O)=O)c2cc(C#N)cc(CCNS(C)(=O)=O)c21', None, None)
('ROB-UNI-b2e39629-4', 'CC(=O)NCCc1c[nH]c2c(CCNS(C)(=O)=O)cc(Cl)cc12', None, None)
('ROB-UNI-b2e39629-5', 'CCn1cc(CCNC(C)=O)c2cc(C#N)cc(CCNS(C)(=O)=O)c21', None, None)
('ROB-UNI-b2e39629-6', 'CC(=O)NCCc1c[nH]c2c(C(C)NC(C)=O)cc(Cl)cc12', None, None)
('ROB-UNI-b2e39629-7', 'CC(=O)NCCc1c[nH]c2c(C(C)NC(C)=O)cc(C#N)cc12', None, None)
('ROB-UNI-b2e39629-8', 'CCn1cc(CCNC(C)=O)c2cc(C#N)cc(C(C)NC(C

In [13]:
import math

database_file = 'assays_database.db'
conn = sqlite3.connect(database_file)
cursor = conn.cursor()

cursor.execute('SELECT * FROM assays')

# Fetch all rows from the result set
rows = cursor.fetchall()

# Iterate through the rows and print the data
for row in rows:

    f_avg_IC50 = row['f_avg_IC50']
    r_avg_IC50 = row['r_avg_IC50']

    if f_avg_IC50 is not None and r_avg_IC50 is not None:

        f_avg_PIC50 = 

# Close the cursor and the connection
cursor.close()
conn.close()


('ANT-DIA-3c79be55-1', 'N#Cc1ccccc1NC(=O)Cc1c[nH]c2ncccc12', 2, 3, 276.29900000000004, 2.61578)
('ANT-DIA-3c79be55-2', 'N#Cc1ccccc1NC(=O)Cc1cccnc1', 1, 3, 237.262, 2.13448)
('ANT-DIA-3c79be55-3', 'CCNc1ccc(C#N)c(NC(=O)Cc2c[nH]c3ncccc23)c1', 3, 4, 319.368, 3.04758)
('ANT-DIA-3c79be55-4', 'CS(=O)(=O)Cc1ccc(C(=O)Nc2cccnc2)o1', 1, 5, 280.305, 1.4715)
('ANT-DIA-3c79be55-5', 'O=C(Nc1cccnc1)c1ccc(N2CCC(O)CC2)o1', 2, 5, 287.319, 1.888)
('ROB-UNI-b2e39629-1', 'CCNc1ccc(C#N)cc1CCNS(C)(=O)=O', 2, 4, 267.35400000000004, 1.08178)
('ROB-UNI-b2e39629-2', 'CS(=O)(=O)NCCc1c[nH]c2c(CCNS(C)(=O)=O)cc(Cl)cc12', 3, 4, 393.918, 1.0047)
('ROB-UNI-b2e39629-3', 'CCn1cc(CCNS(C)(=O)=O)c2cc(C#N)cc(CCNS(C)(=O)=O)c21', 2, 6, 412.537, 0.716280000000001)
('ROB-UNI-b2e39629-4', 'CC(=O)NCCc1c[nH]c2c(CCNS(C)(=O)=O)cc(Cl)cc12', 3, 3, 357.86300000000006, 1.5916)
('ROB-UNI-b2e39629-5', 'CCn1cc(CCNC(C)=O)c2cc(C#N)cc(CCNS(C)(=O)=O)c21', 2, 5, 376.482, 1.30318)
('ROB-UNI-b2e39629-6', 'CC(=O)NCCc1c[nH]c2c(C(C)NC(C)=O)cc(Cl)cc12